In [1]:
import os
import h5py
import numpy as np
from PIL import Image

In [3]:
def norm_0_to_1(img):
    img         = np.float32(img)
    img_flat    = img.flatten()
    max_value   = np.max(img_flat)
    min_value   = np.min(img_flat)
    
    img_normed  = (img - min_value) * 1 / (max_value - min_value)
    
    return img_normed

In [19]:
def save_image_to_h5(scene_index, in_dir, out_path, patch_size=None):
    under_path = os.path.join(in_dir, scene_index, 'under.jpg')
    over_path = os.path.join(in_dir, scene_index, 'over.jpg')
    label_path = os.path.join(in_dir, 'Label', f'{scene_index}.JPG')
    
    under_img = Image.open(under_path).convert('RGB')
    over_img = Image.open(over_path).convert('RGB')
    label_img = Image.open(label_path).convert('RGB')
    
    under_img = norm_0_to_1(np.array(under_img))
    over_img = norm_0_to_1(np.array(over_img))
    label_img = norm_0_to_1(np.array(label_img))
    
    assert(under_img.shape == over_img.shape)
    assert(under_img.shape == label_img.shape)
    
    print(f"[INFO]   under_image : {under_img.shape}")
    print(f"[INFO]   over_image : {over_img.shape}")
    print(f"[INFO]   label_image : {label_img.shape}")
    
    under_img = np.transpose(under_img, (2, 1, 0))  # c, w, h
    over_img = np.transpose(over_img, (2, 1, 0))
    label_img = np.transpose(label_img, (2, 1, 0))
    
    in_data = np.concatenate([under_img, over_img], axis=0)
    w, h = in_data.shape[1], in_data.shape[2]
    num_patch = (w//patch_size) * (h//patch_size)
    
    if patch_size is not None:
        patch_idx = 0
        
        for i in range(0, h, patch_size):
            for j in range(0, w, patch_size):
                if i + patch_size > h or j + patch_size > w:
                    continue
                in_data_patch = in_data[:, j:j+patch_size, i:i+patch_size]
                label_img_patch = label_img[:, j:j+patch_size, i:i+patch_size]
                
                out_file = os.path.join(out_path, f'{scene_index}_{patch_idx}.h5')
                with h5py.File(out_file, 'w') as f:
                    f.create_dataset("IN", data=in_data_patch, dtype=np.float32)
                    f.create_dataset("GT", data=label_img_patch, dtype=np.float32)
                patch_idx += 1
                
                print(f"[INFO] {patch_idx}/{num_patch} of Index {scene_index} H5 saved.")
                print(f"[INFO]   IN : {in_data_patch.shape}")
                print(f"[INFO]   GT : {label_img_patch.shape}")
                    
    else:
        out_file = os.path.join(out_path, f'{scene_index}.h5')
        with h5py.File(out_file, 'w') as f:
            f.create_dataset("IN", data=in_data, dtype=np.float32)
            f.create_dataset("GT", data=label_img, dtype=np.float32)
    
        print(f"[INFO] Index {scene_index} H5 saved.")
        print(f"[INFO]   IN : {in_data.shape}")
        print(f"[INFO]   GT : {label_img.shape}")


In [11]:
jpg_dir = './dataset_sice/test'
h5_dir = './dataset_sice/test_h5'

if not os.path.exists(h5_dir):
    os.makedirs(h5_dir)
    
scene_dirs = [d for d in os.listdir(jpg_dir) if d!='Label']
scene_dirs = sorted(scene_dirs, key=lambda i: int(os.path.splitext(os.path.basename(i))[0]))
num_scenes = len(scene_dirs)
count = 1

print(f"[INFO] {num_scenes} scenes detected in {jpg_dir}.")

for i in range(num_scenes):
    scene_index = scene_dirs[i]
    print(f"[INFO] Load Index {scene_index} ({count}/{num_scenes})")
    save_image_to_h5(scene_index, jpg_dir, h5_dir)
    count += 1
    print()

[INFO] 72 scenes detected in ./dataset_sice/test.
[INFO] Index 3 loaded.
[INFO]   under_image : (2145, 3467, 3)
[INFO]   over_image : (2145, 3467, 3)
[INFO]   label_image : (2145, 3467, 3)
[INFO] Index 3 H5 saved.
[INFO]   IN : (6, 3467, 2145)
[INFO]   GT : (3, 3467, 2145)

[INFO] Index 13 loaded.
[INFO]   under_image : (4000, 6000, 3)
[INFO]   over_image : (4000, 6000, 3)
[INFO]   label_image : (4000, 6000, 3)
[INFO] Index 13 H5 saved.
[INFO]   IN : (6, 6000, 4000)
[INFO]   GT : (3, 6000, 4000)

[INFO] Index 23 loaded.
[INFO]   under_image : (2736, 3648, 3)
[INFO]   over_image : (2736, 3648, 3)
[INFO]   label_image : (2736, 3648, 3)
[INFO] Index 23 H5 saved.
[INFO]   IN : (6, 3648, 2736)
[INFO]   GT : (3, 3648, 2736)

[INFO] Index 32 loaded.
[INFO]   under_image : (1536, 2048, 3)
[INFO]   over_image : (1536, 2048, 3)
[INFO]   label_image : (1536, 2048, 3)
[INFO] Index 32 H5 saved.
[INFO]   IN : (6, 2048, 1536)
[INFO]   GT : (3, 2048, 1536)

[INFO] Index 33 loaded.
[INFO]   under_image

In [20]:
jpg_dir = './dataset_sice/train'
h5_dir = './dataset_sice/train_h5'

if not os.path.exists(h5_dir):
    os.makedirs(h5_dir)
    
scene_dirs = [d for d in os.listdir(jpg_dir) if d!='Label']
scene_dirs = sorted(scene_dirs, key=lambda i: int(os.path.splitext(os.path.basename(i))[0]))
num_scenes = len(scene_dirs)
count = 1

print(f"[INFO] {num_scenes} scenes detected in {jpg_dir}.")

for i in range(num_scenes):
    scene_index = scene_dirs[i]
    print(f"[INFO] Load Index {scene_index} ({count}/{num_scenes})")
    save_image_to_h5(scene_index, jpg_dir, h5_dir, patch_size=256)
    count += 1
    print()

[INFO] 288 scenes detected in ./dataset_sice/train.
[INFO] Load Index 1 (1/288)
[INFO]   under_image : (3456, 5184, 3)
[INFO]   over_image : (3456, 5184, 3)
[INFO]   label_image : (3456, 5184, 3)
[INFO] 1/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 2/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 3/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 4/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 5/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 6/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 7/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 8/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256, 256)
[INFO] 9/260 of Index 1 H5 saved.
[INFO]   IN : (6, 256, 256)
[INFO]   GT : (3, 256,

In [ ]:
## Test set resize to 